In [1]:
# import logging

# from absl import app
# from absl import flags
# import apache_beam as beam
import xarray as xr
# import xarray_beam as xbeam
import xee

import ee
import geemap

import pyproj

import os
import xarray as xr
import geopandas as gp
import pandas as pd
import numpy as np
# import sparse

import hvplot.pandas
import hvplot.xarray
import dask
import cf_xarray

from pynhd import NLDI, WaterData
import intake
import cartopy.crs as ccrs
from shapely.geometry import Polygon

import time
import dask
import requests
import dask.array as da
from dask import delayed
from dask.distributed import Client

import requests
# from IPython.display import HTML
import warnings
from IPython.display import HTML

# from pynhd import NLDI, WaterData
import matplotlib.pyplot as plt
import geopandas as gpd
# import contextily as ctx
from scipy.stats import linregress

/home/kdoore/software/miniforge3/envs/conus404/lib/python3.12/site-packages/numpy/_core/getlimits.py:545: UserWarning: Signature b'\x00\xd0\xcc\xcc\xcc\xcc\xcc\xcc\xfb\xbf\x00\x00\x00\x00\x00\x00' for <class 'numpy.longdouble'> does not match any known type: falling back to type probe function.
This warnings indicates broken support for the dtype!
  machar = _get_machar(dtype)


In [2]:
geemap.ee_initialize()
ee.Initialize()

Enter verification code:  4/1AQlEd8zD7fGROvixRF7UgjAMm1c7EFMGdwFPa1pyOMzAIIera_peGau2u8A



Successfully saved authorization token.


In [8]:
client = Client()  # Starts the Dask client and connects it to the notebook
client

C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\distributed\node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 63200 instead
  warnings.warn(


<Client: 'tcp://127.0.0.1:63201' processes=4 threads=8, memory=31.94 GiB>

# CONUS404

In [3]:
# open the hytest data intake catalog
hytest_cat = intake.open_catalog("https://raw.githubusercontent.com/hytest-org/hytest/main/dataset_catalog/hytest_intake_catalog.yml")
list(hytest_cat)

# open the conus404 sub-catalog
# cat = hytest_cat['conus404-catalog']
cat = hytest_cat['conus404-catalog']
list(cat)

## Select the dataset you want to read into your notebook and preview its metadata
#  conus404-daily-osn
dataset = 'conus404-daily-osn' 
cat[dataset]

print(f"Reading {dataset} metadata...", end='')
ds = cat[dataset].to_dask().metpy.parse_cf()
print("done")
ds
# ds_conus = ds.ACRAINLSM.sel(time=slice('2010-01-01','2020-12-31')).load()
ds_conus = ds.sel(time=slice('2021-01-01','2022-01-01'))
# ds_conus = ds[['ACRAINLSM']].sel(time=slice('1986-01-01','2020-12-31'))
ds_conus

Reading conus404-daily-osn metadata...

/home/kdoore/software/miniforge3/envs/conus404/lib/python3.12/site-packages/intake_xarray/base.py:21: FutureWarning: The return type of `Dataset.dims` will be changed to return a set of dimension names in future, in order to be more consistent with `DataArray.dims`. To access a mapping from dimension names to lengths, please use `Dataset.sizes`.
  'dims': dict(self._ds.dims),


done


<xarray.Dataset> Size: 216GB
Dimensions:         (y: 1015, x: 1367, time: 366, bottom_top_stag: 51,
                     bottom_top: 50, soil_layers_stag: 4, x_stag: 1368,
                     y_stag: 1016, snow_layers_stag: 3, snso_layers_stag: 7)
Coordinates:
    lat             (y, x) float32 6MB dask.array<chunksize=(350, 350), meta=np.ndarray>
    lon             (y, x) float32 6MB dask.array<chunksize=(350, 350), meta=np.ndarray>
  * time            (time) datetime64[ns] 3kB 2021-01-01 ... 2022-01-01
  * x               (x) float64 11kB -2.732e+06 -2.728e+06 ... 2.732e+06
  * y               (y) float64 8kB -2.028e+06 -2.024e+06 ... 2.028e+06
    metpy_crs       object 8B Projection: lambert_conformal_conic
    lat_u           (y, x_stag) float32 6MB dask.array<chunksize=(350, 175), meta=np.ndarray>
    lon_u           (y, x_stag) float32 6MB dask.array<chunksize=(350, 175), meta=np.ndarray>
    lat_v           (y_stag, x) float32 6MB dask.array<chunksize=(175, 350), meta=np.ndarray>
    lon_v           (y_stag, x) float32 6MB dask.array<chunksize=(175, 350), meta=np.ndarray>
Dimensions without coordinates: bottom_top_stag, bottom_top, soil_layers_stag,
                                x_stag, y_stag, snow_layers_stag,
                                snso_layers_stag
Data variables: (12/153)
    ACDEWC          (time, y, x) float32 2GB dask.array<chunksize=(16, 350, 350), meta=np.ndarray>
    ACDRIPR         (time, y, x) float32 2GB dask.array<chunksize=(16, 350, 350), meta=np.ndarray>
    ACDRIPS         (time, y, x) float32 2GB dask.array<chunksize=(16, 350, 350), meta=np.ndarray>
    ACECAN          (time, y, x) float32 2GB dask.array<chunksize=(16, 350, 350), meta=np.ndarray>
    ACEDIR          (time, y, x) float32 2GB dask.array<chunksize=(16, 350, 350), meta=np.ndarray>
    ACETLSM         (time, y, x) float32 2GB dask.array<chunksize=(16, 350, 350), meta=np.ndarray>
    ...              ...
    ZNU             (bottom_top) float32 200B dask.array<chunksize=(50,), meta=np.ndarray>
    ZNW             (bottom_top_stag) float32 204B dask.array<chunksize=(51,), meta=np.ndarray>
    ZS              (soil_layers_stag) float32 16B dask.array<chunksize=(4,), meta=np.ndarray>
    ZSNSO           (time, snso_layers_stag, y, x) float32 14GB dask.array<chunksize=(16, 7, 350, 350), meta=np.ndarray>
    ZWT             (time, y, x) float32 2GB dask.array<chunksize=(16, 350, 350), meta=np.ndarray>
    crs             int64 8B ...
Attributes: (12/148)
    AER_ANGEXP_OPT:                  1
    AER_ANGEXP_VAL:                  1.2999999523162842
    AER_AOD550_OPT:                  1
    AER_AOD550_VAL:                  0.11999999731779099
    AER_ASY_OPT:                     1
    AER_ASY_VAL:                     0.8999999761581421
    ...                              ...
    WEST-EAST_PATCH_START_STAG:      1
    WEST-EAST_PATCH_START_UNSTAG:    1
    W_DAMPING:                       1
    YSU_TOPDOWN_PBLMIX:              0
    history:                         Tue Mar 29 16:35:22 2022: ncrcat -A -vW ...
    history_of_appended_files:       Tue Mar 29 16:35:22 2022: Appended file ...

In [4]:
ds_conus.crs

<xarray.DataArray 'crs' ()> Size: 8B
[1 values with dtype=int64]
Coordinates:
    metpy_crs  object 8B Projection: lambert_conformal_conic
Attributes: (12/16)
    crs_wkt:                        PROJCRS["unknown",BASEGEOGCRS["unknown",D...
    false_easting:                  0.0
    false_northing:                 0.0
    geographic_crs_name:            unknown
    grid_mapping_name:              lambert_conformal_conic
    horizontal_datum_name:          unknown
    ...                             ...
    prime_meridian_name:            Greenwich
    projected_crs_name:             unknown
    reference_ellipsoid_name:       unknown
    semi_major_axis:                6370000.0
    semi_minor_axis:                6370000.0
    standard_parallel:              [30.0, 50.0]

In [6]:
# ds_Pr = ds_conus['ACRAINLSM'].rio.write_crs(ds_conus.crs.metpy.cartopy_crs).drop_vars(['lat', 'lon']).rio.reproject('EPSG:4326')
ds_Pr = ds_conus['ACRAINLSM'].resample(time="YE").sum()
ds_Pr = ds_Pr.rio.write_crs(ds_conus.crs.metpy.cartopy_crs).drop_vars(['lat', 'lon']).compute()
ds_Pr

<xarray.DataArray 'ACRAINLSM' (time: 2, y: 1015, x: 1367)> Size: 11MB
array([[[0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         0.0000000e+00, 0.0000000e+00, 0.0000000e+00],
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         0.0000000e+00, 0.0000000e+00, 0.0000000e+00],
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         0.0000000e+00, 0.0000000e+00, 0.0000000e+00],
        ...,
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         2.1316652e+02, 1.4690875e+02, 0.0000000e+00],
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         1.7235390e+02, 1.2517727e+02, 0.0000000e+00],
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         0.0000000e+00, 0.0000000e+00, 0.0000000e+00]],

       [[0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         0.0000000e+00, 0.0000000e+00, 0.0000000e+00],
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         0.0000000e+00, 0.0000000e+00, 0.0000000e+00],
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         0.0000000e+00, 0.0000000e+00, 0.0000000e+00],
        ...,
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         4.2244030e-10, 0.0000000e+00, 0.0000000e+00],
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         5.9439792e-10, 9.5189901e-14, 0.0000000e+00],
        [0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ...,
         0.0000000e+00, 0.0000000e+00, 0.0000000e+00]]], dtype=float32)
Coordinates:
  * x          (x) float64 11kB -2.732e+06 -2.728e+06 ... 2.728e+06 2.732e+06
  * y          (y) float64 8kB -2.028e+06 -2.024e+06 ... 2.024e+06 2.028e+06
    metpy_crs  object 8B Projection: lambert_conformal_conic
  * time       (time) datetime64[ns] 16B 2021-12-31 2022-12-31
    crs        int64 8B 0
Attributes:
    description:         acccumlated RAINLSM
    integration_length:  24-hour accumulation
    long_name:           Accumulated liquid precipitation into land surface m...
    units:               mm

In [7]:
ds_Pr.crs

<xarray.DataArray 'crs' ()> Size: 8B
array(0)
Coordinates:
    metpy_crs  object 8B Projection: lambert_conformal_conic
    crs        int64 8B 0
Attributes: (12/17)
    crs_wkt:                        PROJCS["unknown",GEOGCS["unknown",DATUM["...
    semi_major_axis:                6370000.0
    semi_minor_axis:                6370000.0
    inverse_flattening:             0.0
    reference_ellipsoid_name:       unknown
    longitude_of_prime_meridian:    0.0
    ...                             ...
    standard_parallel:              (30.0, 50.0)
    latitude_of_projection_origin:  39.1000061035156
    longitude_of_central_meridian:  -97.9000015258789
    false_easting:                  0.0
    false_northing:                 0.0
    spatial_ref:                    PROJCS["unknown",GEOGCS["unknown",DATUM["...

In [21]:
ds_Pr.hvplot.quadmesh(x='x', y='y', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)

:DynamicMap   [time]
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [x,y]   (Accumulated liquid precipitation into land surface model)

In [9]:
# print(ds_Pr['x'].values, ds_Pr['y'].values)
print(ds_Pr.min().values, ds_Pr.max().values)


0.0 9675.524


In [12]:
# Replace fill values with NaN before reprojection
print('Number of NaNs: ', ds_Pr.isnull().sum().values)
# ds_Pr_cleaned = ds_Pr.where(ds_Pr != 0, other=np.nan)

Number of NaNs:  0


In [13]:
ds_Pr_reproj = ds_Pr.rio.reproject('EPSG:4326')

In [14]:
ds_Pr_reproj
# print(ds_Pr_reproj['x'].values, ds_Pr_reproj['y'].values)
# print(ds_Pr_reproj.min().values, ds_Pr_reproj.max().values)


<xarray.DataArray 'ACRAINLSM' (time: 2, y: 916, x: 1884)> Size: 14MB
array([[[nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        ...,
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan]],

       [[nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        ...,
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan]]], dtype=float32)
Coordinates:
  * x          (x) float64 15kB -138.7 -138.7 -138.7 ... -57.12 -57.08 -57.04
  * y          (y) float64 7kB 57.34 57.3 57.25 57.21 ... 17.72 17.68 17.63
    metpy_crs  object 8B Projection: lambert_conformal_conic
  * time       (time) datetime64[ns] 16B 2021-12-31 2022-12-31
    crs        int64 8B 0
Attributes:
    description:         acccumlated RAINLSM
    integration_length:  24-hour accumulation
    long_name:           Accumulated liquid precipitation into land surface m...
    units:               mm
    _FillValue:          nan

ds_Pr_C = (ds_conus['ACRAINLSM'].resample(time="Y", loffset="Y").sum())
ds_Pr_C.rio.write_crs(ds_conus.crs.metpy.cartopy_crs).drop_vars(['lat', 'lon']).rio.reproject('EPSG:4326')

In [15]:
ds_Pr_reproj.rio.crs

CRS.from_epsg(4326)

In [19]:
ds_Pr_reproj.hvplot.quadmesh(x='x', y='y', project=True, rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)

:DynamicMap   [time]
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [x,y]   (Accumulated liquid precipitation into land surface model)